### Import lib

In [1]:
%load_ext lab_black

In [2]:
import os

os.chdir("/cerea_raid/users/dumontj/dev/coco2/dl")
import numpy as np
import sys
import pandas as pd
import xarray as xr
import tensorflow as tf
from sklearn import preprocessing
import matplotlib.pyplot as plt
import seaborn as sns

import matplotlib_functions

matplotlib_functions.setMatplotlibParam()
plt.viridis()
import joblib
import pickle
from include.generators import Generator
from saver import Saver
from include.callbacks import get_modelcheckpoint, ExtraValidation

import model_eval
from Data import Data_train, Data_eval
import wandb
from wandb.keras import WandbCallback, WandbMetricsLogger
import models.reg as rm
from include.loss import rmae
from include.loss import rmae

2023-02-20 11:37:20.734424: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  SSE4.1 SSE4.2 AVX AVX2 AVX512F FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


<Figure size 1920x1440 with 0 Axes>

In [3]:
generator = tf.keras.preprocessing.image.ImageDataGenerator(
    rotation_range=180,
    width_shift_range=0.2,
    height_shift_range=0.2,
    horizontal_flip=True,
    vertical_flip=True,
    shear_range=45,
    zoom_range=0.2,
)

In [4]:
general_save_dir = "/cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/"
project_name = "exp_inputs_pat"

### Data download

In [5]:
path_train_nc = "/libre/dumontj/coco2/dl-input/2km_forPat_2/train_dataset.nc"
path_valid_nc = "/libre/dumontj/coco2/dl-input/2km_forPat_2/valid_dataset.nc"
path_extra_valid_nc = "/libre/dumontj/coco2/dl-input/2km_Pat/valid_dataset.nc"

save_dir = os.path.join(general_save_dir, "pat")

# PLUME

In [6]:
data = Data_train(path_train_nc, path_valid_nc, path_extra_valid_nc)
data.prepare_input("plume")
data.prepare_output_inversion()

data.x.train.shape (12576, 64, 64, 1)


## EfficientNetB0 - no gen

In [7]:
exp_name = "plume_Eff_nogen"
wandb.init(project=project_name, name=exp_name)

Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: Currently logged in as: joffreydumont (cerea-daml). Use `wandb login --relogin` to force relogin


In [8]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [9]:
model_builder = rm.Keras_reg_model_builder("EfficientNetB0", data.x.train.shape[1:], 1)
model = model_builder.get_model()
model.compile("adam", loss=tf.keras.losses.MeanAbsoluteError())

2023-02-13 09:34:03.116182: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  SSE4.1 SSE4.2 AVX AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-02-13 09:34:17.189794: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1613] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 25485 MB memory:  -> device: 0, name: NVIDIA A40, pci bus id: 0000:21:00.0, compute capability: 8.6


### Train 

In [10]:
model.fit(
    data.x.train,
    data.y.train,
    epochs=500,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1,
)

Epoch 1/500


2023-02-13 09:34:30.273865: E tensorflow/core/grappler/optimizers/meta_optimizer.cc:954] layout failed: INVALID_ARGUMENT: Size of values 0 does not match size of permutation 4 @ fanin shape inmodel/efficientnetb0/block2b_drop/dropout/SelectV2-2-TransposeNHWCToNCHW-LayoutOptimizer
2023-02-13 09:34:55.594642: I tensorflow/compiler/xla/stream_executor/cuda/cuda_dnn.cc:428] Loaded cuDNN version 8401
2023-02-13 09:35:18.539993: I tensorflow/tsl/platform/default/subprocess.cc:304] Start cannot spawn child process: No such file or directory
2023-02-13 09:35:20.929530: I tensorflow/compiler/xla/stream_executor/cuda/cuda_blas.cc:630] TensorFloat-32 will be used for the matrix multiplication. This will only be logged once.
2023-02-13 09:35:21.743544: I tensorflow/compiler/xla/service/service.cc:173] XLA service 0x7f8ada8988d0 initialized for platform CUDA (this does not guarantee that XLA will be used). Devices:
2023-02-13 09:35:21.743583: I tensorflow/compiler/xla/service/service.cc:181]   Stre

393/393 [==============================] - ETA: 0s - loss: 3.8738
Epoch 1: val_loss improved from inf to 5.33688, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_Eff_nogen/w_best.h5
extra_val_loss: 1.4520275592803955
393/393 [==============================] - 97s 44ms/step - loss: 3.8738 - val_loss: 5.3369
Epoch 2/500
393/393 [==============================] - ETA: 0s - loss: 2.8868
Epoch 2: val_loss did not improve from 5.33688
extra_val_loss: 1.8317114114761353
393/393 [==============================] - 14s 34ms/step - loss: 2.8868 - val_loss: 5.4245
Epoch 3/500
392/393 [============================>.] - ETA: 0s - loss: 2.8092
Epoch 3: val_loss did not improve from 5.33688
extra_val_loss: 3.102468490600586
393/393 [==============================] - 15s 38ms/step - loss: 2.8078 - val_loss: 6.2284
Epoch 4/500
393/393 [==============================] - ETA: 0s - loss: 2.5587
Epoch 4: val_loss improved from 5.33688 to 2.45140, saving model to /cerea_raid/use

### save

In [11]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))
joblib.dump(data.x.scaler, os.path.join(save_dir, exp_name, "scaler.save"))

['/cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_Eff_nogen/scaler.save']

## EfficientNetB0 - with gen

In [12]:
exp_name = "plume_Eff_gen"
wandb.init(project=project_name, name=exp_name)

In [13]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [14]:
model_builder = rm.Keras_reg_model_builder("EfficientNetB0", data.x.train.shape[1:], 1)
model = model_builder.get_model()
model.compile("adam", loss=tf.keras.losses.MeanAbsoluteError())

### Train 

In [15]:
model.fit(
    generator.flow(data.x.train, data.y.train),
    epochs=1000,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1,
)

Epoch 1/1000


2023-02-13 11:44:20.891765: E tensorflow/core/grappler/optimizers/meta_optimizer.cc:954] layout failed: INVALID_ARGUMENT: Size of values 0 does not match size of permutation 4 @ fanin shape inmodel_1/efficientnetb0/block2b_drop/dropout/SelectV2-2-TransposeNHWCToNCHW-LayoutOptimizer


393/393 [==============================] - ETA: 0s - loss: 4.2316
Epoch 1: val_loss improved from inf to 4.91550, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_Eff_gen/w_best.h5
extra_val_loss: 2.102231025695801
393/393 [==============================] - 39s 53ms/step - loss: 4.2316 - val_loss: 4.9155
Epoch 2/1000
392/393 [============================>.] - ETA: 0s - loss: 3.1995
Epoch 2: val_loss did not improve from 4.91550
extra_val_loss: 2.1254639625549316
393/393 [==============================] - 20s 51ms/step - loss: 3.1995 - val_loss: 5.4380
Epoch 3/1000
392/393 [============================>.] - ETA: 0s - loss: 3.0561
Epoch 3: val_loss improved from 4.91550 to 4.58871, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_Eff_gen/w_best.h5
extra_val_loss: 1.8833814859390259
393/393 [==============================] - 20s 51ms/step - loss: 3.0552 - val_loss: 4.5887
Epoch 4/1000
393/393 [==============================] - ETA:

### save

In [16]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))
joblib.dump(data.x.scaler, os.path.join(save_dir, exp_name, "scaler.save"))

['/cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_Eff_gen/scaler.save']

## Linear baseline

In [17]:
exp_name = "plume_linear"
wandb.init(project=project_name, name=exp_name)

In [18]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [19]:
model = tf.keras.models.Sequential()
model.add(tf.keras.layers.Conv2D(16, (3, 3), input_shape=data.x.fields_input_shape))
model.add(tf.keras.layers.MaxPooling2D((2, 2)))
model.add(tf.keras.layers.Conv2D(16, (3, 3)))
model.add(tf.keras.layers.MaxPooling2D((2, 2)))
model.add(tf.keras.layers.Conv2D(16, (3, 3)))
model.add(tf.keras.layers.Flatten())
model.add(tf.keras.layers.Dense(16))
model.add(tf.keras.layers.Dense(1))

model.compile("adam", loss="MeanAbsoluteError")

### Train 

In [20]:
model.fit(
    data.x.train,
    data.y.train,
    epochs=200,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1,
)

Epoch 1/200
384/393 [============================>.] - ETA: 0s - loss: 3.7989
Epoch 1: val_loss improved from inf to 3.48380, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_linear/w_best.h5
extra_val_loss: 4.0431342124938965
393/393 [==============================] - 3s 5ms/step - loss: 3.7961 - val_loss: 3.4838
Epoch 2/200
382/393 [============================>.] - ETA: 0s - loss: 3.3576
Epoch 2: val_loss did not improve from 3.48380
extra_val_loss: 5.233192443847656
393/393 [==============================] - 2s 4ms/step - loss: 3.3493 - val_loss: 3.5015
Epoch 3/200
379/393 [===========================>..] - ETA: 0s - loss: 3.2980
Epoch 3: val_loss improved from 3.48380 to 3.35223, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_linear/w_best.h5
extra_val_loss: 5.039037227630615
393/393 [==============================] - 2s 4ms/step - loss: 3.2964 - val_loss: 3.3522
Epoch 4/200
380/393 [============================>.] - ETA:

### save

In [21]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))
joblib.dump(data.x.scaler, os.path.join(save_dir, exp_name, "scaler.save"))

['/cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_linear/scaler.save']

## Research of a new model

In [22]:
exp_name = "plume_modelX"
wandb.init(project=project_name, name=exp_name)

In [29]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [30]:
inputs = tf.keras.layers.Input((64, 64, 1))

x = tf.keras.layers.Conv2D(32, kernel_size=(3, 3), activation="elu", strides=1)(inputs)
x = tf.keras.layers.Dropout(0.1)(x)
x = tf.keras.layers.Conv2D(32, kernel_size=(3, 3), activation="elu", strides=1)(x)
x = tf.keras.layers.MaxPooling2D(pool_size=(2, 2), padding="valid", strides=2)(x)
x = tf.keras.layers.BatchNormalization()(x)

x = tf.keras.layers.Conv2D(32, kernel_size=(3, 3), activation="elu", strides=1)(x)
x = tf.keras.layers.Dropout(0.2)(x)
x = tf.keras.layers.Conv2D(64, kernel_size=(3, 3), activation="elu", strides=1)(x)
x = tf.keras.layers.BatchNormalization()(x)

x = tf.keras.layers.Conv2D(64, kernel_size=(3, 3), activation="elu", strides=1)(x)
x = tf.keras.layers.Dropout(0.2)(x)
x = tf.keras.layers.Conv2D(64, kernel_size=(3, 3), activation="elu", strides=1)(x)
x = tf.keras.layers.MaxPooling2D(pool_size=(2, 2), padding="valid", strides=2)(x)

x = tf.keras.layers.Flatten()(x)
x = tf.keras.layers.Dense(1)(x)
outputs = tf.keras.layers.LeakyReLU(alpha=0.3)(x)

model = tf.keras.Model([inputs], outputs)

model.compile("adam", loss="MeanAbsoluteError")

### Train 

In [31]:
model.fit(
    data.x.train,
    data.y.train,
    epochs=500,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1,
)

Epoch 1/500


2023-02-13 17:02:03.593785: E tensorflow/core/grappler/optimizers/meta_optimizer.cc:954] layout failed: INVALID_ARGUMENT: Size of values 0 does not match size of permutation 4 @ fanin shape inmodel_2/dropout/dropout/SelectV2-2-TransposeNHWCToNCHW-LayoutOptimizer


385/393 [============================>.] - ETA: 0s - loss: 3.2812
Epoch 1: val_loss improved from inf to 4.76862, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_modelX/w_best.h5
extra_val_loss: 1.4734357595443726
393/393 [==============================] - 5s 8ms/step - loss: 3.2799 - val_loss: 4.7686
Epoch 2/500
391/393 [============================>.] - ETA: 0s - loss: 2.8799
Epoch 2: val_loss improved from 4.76862 to 2.80202, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_modelX/w_best.h5
extra_val_loss: 4.30399227142334
393/393 [==============================] - 3s 7ms/step - loss: 2.8822 - val_loss: 2.8020
Epoch 3/500
392/393 [============================>.] - ETA: 0s - loss: 2.6751
Epoch 3: val_loss did not improve from 2.80202
extra_val_loss: 3.3590571880340576
393/393 [==============================] - 2s 6ms/step - loss: 2.6763 - val_loss: 2.8067
Epoch 4/500
387/393 [============================>.] - ETA: 0s - loss: 

### save

In [32]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))
joblib.dump(data.x.scaler, os.path.join(save_dir, exp_name, "scaler.save"))

['/cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_modelX/scaler.save']

# PLUME + PLUME PREC

In [33]:
wandb.finish()

In [34]:
data = Data_train(path_train_nc, path_valid_nc, path_extra_valid_nc)
data.prepare_input("plume", "plume_prec")
data.prepare_output_inversion()

data.x.train.shape (12576, 64, 64, 2)


## EfficientNetB0 - no gen

In [35]:
exp_name = "plume_plumeprec_Eff_nogen"
wandb.init(project=project_name, name=exp_name)

In [36]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [37]:
model_builder = rm.Keras_reg_model_builder("EfficientNetB0", data.x.train.shape[1:], 1)
model = model_builder.get_model()
model.compile("adam", loss=tf.keras.losses.MeanAbsoluteError())

/profils_cerea/dumontj/mambaforge/envs/gpu/lib/python3.9/site-packages/keras/applications/efficientnet.py:321: UserWarning: This model usually expects 1 or 3 input channels. However, it was passed an input_shape with 2 input channels.
  input_shape = imagenet_utils.obtain_input_shape(


### Train 

In [38]:
model.fit(
    data.x.train,
    data.y.train,
    epochs=500,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1,
)

Epoch 1/500


2023-02-13 17:24:01.895422: E tensorflow/core/grappler/optimizers/meta_optimizer.cc:954] layout failed: INVALID_ARGUMENT: Size of values 0 does not match size of permutation 4 @ fanin shape inmodel_3/efficientnetb0/block2b_drop/dropout/SelectV2-2-TransposeNHWCToNCHW-LayoutOptimizer


392/393 [============================>.] - ETA: 0s - loss: 3.8849
Epoch 1: val_loss improved from inf to 5.83784, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_Eff_nogen/w_best.h5
extra_val_loss: 1.125948429107666
393/393 [==============================] - 35s 42ms/step - loss: 3.8820 - val_loss: 5.8378
Epoch 2/500
391/393 [============================>.] - ETA: 0s - loss: 2.6429
Epoch 2: val_loss improved from 5.83784 to 3.70024, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_Eff_nogen/w_best.h5
extra_val_loss: 1.3114049434661865
393/393 [==============================] - 11s 27ms/step - loss: 2.6408 - val_loss: 3.7002
Epoch 3/500
393/393 [==============================] - ETA: 0s - loss: 2.5838
Epoch 3: val_loss improved from 3.70024 to 3.39266, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_Eff_nogen/w_best.h5
extra_val_loss: 4.211664199829102
393/393 [========

### save

In [39]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))
joblib.dump(data.x.scaler, os.path.join(save_dir, exp_name, "scaler.save"))

['/cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_Eff_nogen/scaler.save']

## EfficientNetB0 - with gen

In [40]:
exp_name = "plume_plumeprec_Eff_gen"
wandb.init(project=project_name, name=exp_name)

In [41]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [42]:
model_builder = rm.Keras_reg_model_builder("EfficientNetB0", data.x.train.shape[1:], 1)
model = model_builder.get_model()
model.compile("adam", loss=tf.keras.losses.MeanAbsoluteError())

/profils_cerea/dumontj/mambaforge/envs/gpu/lib/python3.9/site-packages/keras/applications/efficientnet.py:321: UserWarning: This model usually expects 1 or 3 input channels. However, it was passed an input_shape with 2 input channels.
  input_shape = imagenet_utils.obtain_input_shape(


### Train 

In [43]:
model.fit(
    generator.flow(data.x.train, data.y.train),
    epochs=1000,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1,
)

Epoch 1/1000


/profils_cerea/dumontj/mambaforge/envs/gpu/lib/python3.9/site-packages/keras/preprocessing/image.py:766: UserWarning: NumpyArrayIterator is set to use the data format convention "channels_last" (channels on axis 3), i.e. expected either 1, 3, or 4 channels on axis 3. However, it was passed an array with shape (12576, 64, 64, 2) (2 channels).
  warnings.warn(
2023-02-13 19:18:55.679682: E tensorflow/core/grappler/optimizers/meta_optimizer.cc:954] layout failed: INVALID_ARGUMENT: Size of values 0 does not match size of permutation 4 @ fanin shape inmodel_4/efficientnetb0/block2b_drop/dropout/SelectV2-2-TransposeNHWCToNCHW-LayoutOptimizer


392/393 [============================>.] - ETA: 0s - loss: 4.1076
Epoch 1: val_loss improved from inf to 4.76746, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_Eff_gen/w_best.h5
extra_val_loss: 2.4644837379455566
393/393 [==============================] - 37s 48ms/step - loss: 4.1077 - val_loss: 4.7675
Epoch 2/1000
393/393 [==============================] - ETA: 0s - loss: 3.1163
Epoch 2: val_loss improved from 4.76746 to 3.98575, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_Eff_gen/w_best.h5
extra_val_loss: 2.68637752532959
393/393 [==============================] - 18s 46ms/step - loss: 3.1163 - val_loss: 3.9857
Epoch 3/1000
392/393 [============================>.] - ETA: 0s - loss: 2.9878
Epoch 3: val_loss improved from 3.98575 to 3.82506, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_Eff_gen/w_best.h5
extra_val_loss: 6.072793006896973
393/393 [=============

### save

In [44]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))
joblib.dump(data.x.scaler, os.path.join(save_dir, exp_name, "scaler.save"))

['/cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_Eff_gen/scaler.save']

## Linear baseline

In [45]:
exp_name = "plume_plumeprec_linear"
wandb.init(project=project_name, name=exp_name)

In [46]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [47]:
model = tf.keras.models.Sequential()
model.add(tf.keras.layers.Conv2D(16, (3, 3), input_shape=data.x.fields_input_shape))
model.add(tf.keras.layers.MaxPooling2D((2, 2)))
model.add(tf.keras.layers.Conv2D(16, (3, 3)))
model.add(tf.keras.layers.MaxPooling2D((2, 2)))
model.add(tf.keras.layers.Conv2D(16, (3, 3)))
model.add(tf.keras.layers.Flatten())
model.add(tf.keras.layers.Dense(16))
model.add(tf.keras.layers.Dense(1))

model.compile("adam", loss="MeanAbsoluteError")

### Train 

In [48]:
model.fit(
    data.x.train,
    data.y.train,
    epochs=200,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1,
)

Epoch 1/200
386/393 [============================>.] - ETA: 0s - loss: 3.7702
Epoch 1: val_loss improved from inf to 3.43660, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_linear/w_best.h5
extra_val_loss: 5.209198951721191
393/393 [==============================] - 3s 5ms/step - loss: 3.7677 - val_loss: 3.4366
Epoch 2/200
391/393 [============================>.] - ETA: 0s - loss: 3.2915
Epoch 2: val_loss improved from 3.43660 to 3.37324, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_linear/w_best.h5
extra_val_loss: 4.31334114074707
393/393 [==============================] - 1s 3ms/step - loss: 3.2905 - val_loss: 3.3732
Epoch 3/200
392/393 [============================>.] - ETA: 0s - loss: 3.1694
Epoch 3: val_loss improved from 3.37324 to 3.19372, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_linear/w_best.h5
extra_val_loss: 3.5492069721221924
393/393 [==========

### save

In [49]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))
joblib.dump(data.x.scaler, os.path.join(save_dir, exp_name, "scaler.save"))

['/cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_linear/scaler.save']

## Research of a new model

In [50]:
exp_name = "plume_plumeprec_modelX"
wandb.init(project=project_name, name=exp_name)

In [51]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [54]:
inputs = tf.keras.layers.Input((64, 64, 2))

x = tf.keras.layers.Conv2D(32, kernel_size=(3, 3), activation="elu", strides=1)(inputs)
x = tf.keras.layers.Dropout(0.1)(x)
x = tf.keras.layers.Conv2D(32, kernel_size=(3, 3), activation="elu", strides=1)(x)
x = tf.keras.layers.MaxPooling2D(pool_size=(2, 2), padding="valid", strides=2)(x)
x = tf.keras.layers.BatchNormalization()(x)

x = tf.keras.layers.Conv2D(32, kernel_size=(3, 3), activation="elu", strides=1)(x)
x = tf.keras.layers.Dropout(0.2)(x)
x = tf.keras.layers.Conv2D(64, kernel_size=(3, 3), activation="elu", strides=1)(x)
x = tf.keras.layers.BatchNormalization()(x)

x = tf.keras.layers.Conv2D(64, kernel_size=(3, 3), activation="elu", strides=1)(x)
x = tf.keras.layers.Dropout(0.2)(x)
x = tf.keras.layers.Conv2D(64, kernel_size=(3, 3), activation="elu", strides=1)(x)
x = tf.keras.layers.MaxPooling2D(pool_size=(2, 2), padding="valid", strides=2)(x)

x = tf.keras.layers.Flatten()(x)
x = tf.keras.layers.Dense(1)(x)
outputs = tf.keras.layers.LeakyReLU(alpha=0.3)(x)

model = tf.keras.Model([inputs], outputs)

model.compile("adam", loss="MeanAbsoluteError")

### Train 

In [55]:
model.fit(
    data.x.train,
    data.y.train,
    epochs=500,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1,
)

Epoch 1/500


2023-02-14 09:06:00.816897: E tensorflow/core/grappler/optimizers/meta_optimizer.cc:954] layout failed: INVALID_ARGUMENT: Size of values 0 does not match size of permutation 4 @ fanin shape inmodel_6/dropout_6/dropout/SelectV2-2-TransposeNHWCToNCHW-LayoutOptimizer


392/393 [============================>.] - ETA: 0s - loss: 3.2014
Epoch 1: val_loss improved from inf to 5.11072, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_modelX/w_best.h5
extra_val_loss: 1.6790190935134888
393/393 [==============================] - 5s 8ms/step - loss: 3.1997 - val_loss: 5.1107
Epoch 2/500
389/393 [============================>.] - ETA: 0s - loss: 2.7937
Epoch 2: val_loss improved from 5.11072 to 4.20102, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_modelX/w_best.h5
extra_val_loss: 3.4179928302764893
393/393 [==============================] - 3s 7ms/step - loss: 2.7969 - val_loss: 4.2010
Epoch 3/500
392/393 [============================>.] - ETA: 0s - loss: 2.6325
Epoch 3: val_loss improved from 4.20102 to 2.50976, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_modelX/w_best.h5
extra_val_loss: 2.556276321411133
393/393 [====================

### save

In [56]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))
joblib.dump(data.x.scaler, os.path.join(save_dir, exp_name, "scaler.save"))

['/cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_modelX/scaler.save']

# PLUME + PLUME PREC + WINDS

In [57]:
data = Data_train(path_train_nc, path_valid_nc, path_extra_valid_nc)
data.prepare_input("plume", "plume_prec", "u_wind", "v_wind")
data.prepare_output_inversion()

data.x.train.shape (12576, 64, 64, 4)


## EfficientNetB0 - no gen

In [58]:
exp_name = "plume_plumeprec_winds_Eff_nogen"
wandb.init(project=project_name, name=exp_name)

In [59]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [60]:
model_builder = rm.Keras_reg_model_builder("EfficientNetB0", data.x.train.shape[1:], 1)
model = model_builder.get_model()
model.compile("adam", loss=tf.keras.losses.MeanAbsoluteError())

/profils_cerea/dumontj/mambaforge/envs/gpu/lib/python3.9/site-packages/keras/applications/efficientnet.py:321: UserWarning: This model usually expects 1 or 3 input channels. However, it was passed an input_shape with 4 input channels.
  input_shape = imagenet_utils.obtain_input_shape(


### Train 

In [61]:
model.fit(
    data.x.train,
    data.y.train,
    epochs=500,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1,
)

Epoch 1/500


2023-02-14 09:30:08.293165: E tensorflow/core/grappler/optimizers/meta_optimizer.cc:954] layout failed: INVALID_ARGUMENT: Size of values 0 does not match size of permutation 4 @ fanin shape inmodel_7/efficientnetb0/block2b_drop/dropout/SelectV2-2-TransposeNHWCToNCHW-LayoutOptimizer


392/393 [============================>.] - ETA: 0s - loss: 3.7354
Epoch 1: val_loss improved from inf to 5.11899, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_winds_Eff_nogen/w_best.h5
extra_val_loss: 1.6940783262252808
393/393 [==============================] - 35s 42ms/step - loss: 3.7330 - val_loss: 5.1190
Epoch 2/500
392/393 [============================>.] - ETA: 0s - loss: 2.4747
Epoch 2: val_loss improved from 5.11899 to 3.04009, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_winds_Eff_nogen/w_best.h5
extra_val_loss: 3.1172056198120117
393/393 [==============================] - 16s 41ms/step - loss: 2.4739 - val_loss: 3.0401
Epoch 3/500
393/393 [==============================] - ETA: 0s - loss: 2.2661
Epoch 3: val_loss improved from 3.04009 to 2.39148, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_winds_Eff_nogen/w_best.h5
extra_val_loss: 2.78655004501342

### save

In [62]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))
joblib.dump(data.x.scaler, os.path.join(save_dir, exp_name, "scaler.save"))

['/cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_winds_Eff_nogen/scaler.save']

## EfficientNetB0 - with gen

In [63]:
exp_name = "plume_plumeprec_winds_Eff_gen"
wandb.init(project=project_name, name=exp_name)

In [64]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [65]:
model_builder = rm.Keras_reg_model_builder("EfficientNetB0", data.x.train.shape[1:], 1)
model = model_builder.get_model()
model.compile("adam", loss=tf.keras.losses.MeanAbsoluteError())

/profils_cerea/dumontj/mambaforge/envs/gpu/lib/python3.9/site-packages/keras/applications/efficientnet.py:321: UserWarning: This model usually expects 1 or 3 input channels. However, it was passed an input_shape with 4 input channels.
  input_shape = imagenet_utils.obtain_input_shape(


### Train 

In [66]:
model.fit(
    generator.flow(data.x.train, data.y.train),
    epochs=1000,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1,
)

Epoch 1/1000


2023-02-14 11:29:35.352561: E tensorflow/core/grappler/optimizers/meta_optimizer.cc:954] layout failed: INVALID_ARGUMENT: Size of values 0 does not match size of permutation 4 @ fanin shape inmodel_8/efficientnetb0/block2b_drop/dropout/SelectV2-2-TransposeNHWCToNCHW-LayoutOptimizer


393/393 [==============================] - ETA: 0s - loss: 4.2097
Epoch 1: val_loss improved from inf to 5.74661, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_winds_Eff_gen/w_best.h5
extra_val_loss: 1.1626697778701782
393/393 [==============================] - 38s 48ms/step - loss: 4.2097 - val_loss: 5.7466
Epoch 2/1000
393/393 [==============================] - ETA: 0s - loss: 3.2693
Epoch 2: val_loss did not improve from 5.74661
extra_val_loss: 6.628417491912842
393/393 [==============================] - 19s 49ms/step - loss: 3.2693 - val_loss: 12.0940
Epoch 3/1000
393/393 [==============================] - ETA: 0s - loss: 2.9518
Epoch 3: val_loss improved from 5.74661 to 2.54298, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_winds_Eff_gen/w_best.h5
extra_val_loss: 4.087485313415527
393/393 [==============================] - 19s 48ms/step - loss: 2.9518 - val_loss: 2.5430
Epoch 4/1000
392/393 [======

### save

In [67]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))
joblib.dump(data.x.scaler, os.path.join(save_dir, exp_name, "scaler.save"))

['/cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_winds_Eff_gen/scaler.save']

## Linear baseline

In [68]:
exp_name = "plume_plumeprec_winds_linear"
wandb.init(project=project_name, name=exp_name)

In [69]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [70]:
model = tf.keras.models.Sequential()
model.add(tf.keras.layers.Conv2D(16, (3, 3), input_shape=data.x.fields_input_shape))
model.add(tf.keras.layers.MaxPooling2D((2, 2)))
model.add(tf.keras.layers.Conv2D(16, (3, 3)))
model.add(tf.keras.layers.MaxPooling2D((2, 2)))
model.add(tf.keras.layers.Conv2D(16, (3, 3)))
model.add(tf.keras.layers.Flatten())
model.add(tf.keras.layers.Dense(16))
model.add(tf.keras.layers.Dense(1))

model.compile("adam", loss="MeanAbsoluteError")

### Train 

In [71]:
model.fit(
    data.x.train,
    data.y.train,
    epochs=200,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1,
)

Epoch 1/200
389/393 [============================>.] - ETA: 0s - loss: 3.8022
Epoch 1: val_loss improved from inf to 3.34809, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_winds_linear/w_best.h5
extra_val_loss: 4.357554912567139
393/393 [==============================] - 3s 6ms/step - loss: 3.7945 - val_loss: 3.3481
Epoch 2/200
388/393 [============================>.] - ETA: 0s - loss: 3.2755
Epoch 2: val_loss improved from 3.34809 to 3.18400, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_winds_linear/w_best.h5
extra_val_loss: 4.858384609222412
393/393 [==============================] - 2s 5ms/step - loss: 3.2762 - val_loss: 3.1840
Epoch 3/200
391/393 [============================>.] - ETA: 0s - loss: 3.0924
Epoch 3: val_loss improved from 3.18400 to 3.13276, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_winds_linear/w_best.h5
extra_val_loss: 4.386847019195557
3

### save

In [72]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))
joblib.dump(data.x.scaler, os.path.join(save_dir, exp_name, "scaler.save"))

['/cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_winds_linear/scaler.save']

## Research of a new model

In [73]:
exp_name = "plume_plumeprec_winds_modelX"
wandb.init(project=project_name, name=exp_name)

In [74]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [75]:
inputs = tf.keras.layers.Input((64, 64, 4))

x = tf.keras.layers.Conv2D(32, kernel_size=(3, 3), activation="elu", strides=1)(inputs)
x = tf.keras.layers.Dropout(0.1)(x)
x = tf.keras.layers.Conv2D(32, kernel_size=(3, 3), activation="elu", strides=1)(x)
x = tf.keras.layers.MaxPooling2D(pool_size=(2, 2), padding="valid", strides=2)(x)
x = tf.keras.layers.BatchNormalization()(x)

x = tf.keras.layers.Conv2D(32, kernel_size=(3, 3), activation="elu", strides=1)(x)
x = tf.keras.layers.Dropout(0.2)(x)
x = tf.keras.layers.Conv2D(64, kernel_size=(3, 3), activation="elu", strides=1)(x)
x = tf.keras.layers.BatchNormalization()(x)

x = tf.keras.layers.Conv2D(64, kernel_size=(3, 3), activation="elu", strides=1)(x)
x = tf.keras.layers.Dropout(0.2)(x)
x = tf.keras.layers.Conv2D(64, kernel_size=(3, 3), activation="elu", strides=1)(x)
x = tf.keras.layers.MaxPooling2D(pool_size=(2, 2), padding="valid", strides=2)(x)

x = tf.keras.layers.Flatten()(x)
x = tf.keras.layers.Dense(1)(x)
outputs = tf.keras.layers.LeakyReLU(alpha=0.3)(x)

model = tf.keras.Model([inputs], outputs)

model.compile("adam", loss="MeanAbsoluteError")

### Train 

In [76]:
model.fit(
    data.x.train,
    data.y.train,
    epochs=500,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1,
)

Epoch 1/500


2023-02-14 16:50:44.540158: E tensorflow/core/grappler/optimizers/meta_optimizer.cc:954] layout failed: INVALID_ARGUMENT: Size of values 0 does not match size of permutation 4 @ fanin shape inmodel_9/dropout_9/dropout/SelectV2-2-TransposeNHWCToNCHW-LayoutOptimizer


392/393 [============================>.] - ETA: 0s - loss: 3.1743
Epoch 1: val_loss improved from inf to 4.20777, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_winds_modelX/w_best.h5
extra_val_loss: 1.777710199356079
393/393 [==============================] - 5s 9ms/step - loss: 3.1729 - val_loss: 4.2078
Epoch 2/500
390/393 [============================>.] - ETA: 0s - loss: 2.6472
Epoch 2: val_loss improved from 4.20777 to 2.86670, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_winds_modelX/w_best.h5
extra_val_loss: 1.9943559169769287
393/393 [==============================] - 5s 12ms/step - loss: 2.6481 - val_loss: 2.8667
Epoch 3/500
388/393 [============================>.] - ETA: 0s - loss: 2.4512
Epoch 3: val_loss improved from 2.86670 to 2.68814, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_winds_modelX/w_best.h5
extra_val_loss: 1.9312795400619507
393/393 [=

### save

In [77]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))
joblib.dump(data.x.scaler, os.path.join(save_dir, exp_name, "scaler.save"))

['/cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_plumeprec_winds_modelX/scaler.save']

# FIELD NOT NOISY + PERFECT SEG + FIELD PREC + WINDS

In [10]:
data = Data_train(path_train_nc, path_valid_nc, path_extra_valid_nc)
data.prepare_input(
    "xco2_noiseless", "weighted_plume", "xco2_noiseless_prec", "u_wind", "v_wind"
)
data.prepare_output_inversion()

data.x.train.shape (12576, 64, 64, 5)


## EfficientNetB0 - no gen

In [11]:
exp_name = "xco2noiseless_prec_plume_winds_Eff_nogen"
wandb.init(project=project_name, name=exp_name)

Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: Currently logged in as: joffreydumont (cerea-daml). Use `wandb login --relogin` to force relogin


In [12]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [13]:
model_builder = rm.Keras_reg_model_builder("EfficientNetB0", data.x.train.shape[1:], 1)
model = model_builder.get_model()
model.compile("adam", loss=tf.keras.losses.MeanAbsoluteError())

/profils_cerea/dumontj/mambaforge/envs/gpu/lib/python3.9/site-packages/keras/applications/efficientnet.py:321: UserWarning: This model usually expects 1 or 3 input channels. However, it was passed an input_shape with 5 input channels.
  input_shape = imagenet_utils.obtain_input_shape(
2023-02-14 17:30:38.425211: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  SSE4.1 SSE4.2 AVX AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-02-14 17:30:38.846126: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1613] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 43491 MB memory:  -> device: 0, name: NVIDIA A40, pci bus id: 0000:21:00.0, compute capability: 8.6


### Train 

In [14]:
model.fit(
    data.x.train,
    data.y.train,
    epochs=500,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1,
)

Epoch 1/500


2023-02-14 17:30:49.392740: E tensorflow/core/grappler/optimizers/meta_optimizer.cc:954] layout failed: INVALID_ARGUMENT: Size of values 0 does not match size of permutation 4 @ fanin shape inmodel/efficientnetb0/block2b_drop/dropout/SelectV2-2-TransposeNHWCToNCHW-LayoutOptimizer
2023-02-14 17:30:51.137601: I tensorflow/compiler/xla/stream_executor/cuda/cuda_dnn.cc:428] Loaded cuDNN version 8401
2023-02-14 17:30:52.012938: I tensorflow/tsl/platform/default/subprocess.cc:304] Start cannot spawn child process: No such file or directory
2023-02-14 17:30:52.104207: I tensorflow/compiler/xla/stream_executor/cuda/cuda_blas.cc:630] TensorFloat-32 will be used for the matrix multiplication. This will only be logged once.
2023-02-14 17:30:52.109737: I tensorflow/compiler/xla/service/service.cc:173] XLA service 0x7fac71f7ad70 initialized for platform CUDA (this does not guarantee that XLA will be used). Devices:
2023-02-14 17:30:52.109758: I tensorflow/compiler/xla/service/service.cc:181]   Stre

393/393 [==============================] - ETA: 0s - loss: 4.1489
Epoch 1: val_loss improved from inf to 4.19172, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/xco2noiseless_prec_plume_winds_Eff_nogen/w_best.h5
extra_val_loss: 5.032594680786133
393/393 [==============================] - 39s 45ms/step - loss: 4.1489 - val_loss: 4.1917
Epoch 2/500
392/393 [============================>.] - ETA: 0s - loss: 3.1179
Epoch 2: val_loss improved from 4.19172 to 2.89161, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/xco2noiseless_prec_plume_winds_Eff_nogen/w_best.h5
extra_val_loss: 6.096453666687012
393/393 [==============================] - 16s 42ms/step - loss: 3.1184 - val_loss: 2.8916
Epoch 3/500
393/393 [==============================] - ETA: 0s - loss: 2.8366
Epoch 3: val_loss did not improve from 2.89161
extra_val_loss: 7.48310661315918
393/393 [==============================] - 15s 38ms/step - loss: 2.8366 - val_loss: 3.3157
Epoch 4/500

### save

In [15]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))
joblib.dump(data.x.scaler, os.path.join(save_dir, exp_name, "scaler.save"))

['/cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/xco2noiseless_prec_plume_winds_Eff_nogen/scaler.save']

## EfficientNetB0 - with gen

In [26]:
exp_name = "xco2noiseless_prec_plume_winds_Eff_gen"
wandb.init(project=project_name, name=exp_name)

In [27]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [28]:
model_builder = rm.Keras_reg_model_builder("EfficientNetB0", data.x.train.shape[1:], 1)
model = model_builder.get_model()
model.compile("adam", loss=tf.keras.losses.MeanAbsoluteError())

/profils_cerea/dumontj/mambaforge/envs/gpu/lib/python3.9/site-packages/keras/applications/efficientnet.py:321: UserWarning: This model usually expects 1 or 3 input channels. However, it was passed an input_shape with 5 input channels.
  input_shape = imagenet_utils.obtain_input_shape(


### Train 

In [ ]:
model.fit(
    generator.flow(data.x.train, data.y.train),
    epochs=1000,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1
)

### save

In [ ]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))
joblib.dump(data.x.scaler, os.path.join(save_dir, exp_name, "scaler.save"))

## Linear baseline

In [16]:
exp_name = "xco2noiseless_prec_plume_winds__linear"
wandb.init(project=project_name, name=exp_name)

In [17]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [18]:
model = tf.keras.models.Sequential()
model.add(tf.keras.layers.Conv2D(16, (3, 3), input_shape=data.x.fields_input_shape))
model.add(tf.keras.layers.MaxPooling2D((2, 2)))
model.add(tf.keras.layers.Conv2D(16, (3, 3)))
model.add(tf.keras.layers.MaxPooling2D((2, 2)))
model.add(tf.keras.layers.Conv2D(16, (3, 3)))
model.add(tf.keras.layers.Flatten())
model.add(tf.keras.layers.Dense(16))
model.add(tf.keras.layers.Dense(1))

model.compile("adam", loss="MeanAbsoluteError")

### Train 

In [19]:
model.fit(
    data.x.train,
    data.y.train,
    epochs=200,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1,
)

Epoch 1/200
383/393 [============================>.] - ETA: 0s - loss: 3.8414
Epoch 1: val_loss improved from inf to 3.19575, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/xco2noiseless_prec_plume_winds__linear/w_best.h5
extra_val_loss: 5.882327079772949
393/393 [==============================] - 4s 6ms/step - loss: 3.8252 - val_loss: 3.1958
Epoch 2/200
387/393 [============================>.] - ETA: 0s - loss: 3.2196
Epoch 2: val_loss improved from 3.19575 to 2.99504, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/xco2noiseless_prec_plume_winds__linear/w_best.h5
extra_val_loss: 6.688746929168701
393/393 [==============================] - 2s 6ms/step - loss: 3.2143 - val_loss: 2.9950
Epoch 3/200
382/393 [============================>.] - ETA: 0s - loss: 3.0127
Epoch 3: val_loss improved from 2.99504 to 2.97548, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/xco2noiseless_prec_plume_winds__linear/w_best.h5
extra

### save

In [20]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))
joblib.dump(data.x.scaler, os.path.join(save_dir, exp_name, "scaler.save"))

['/cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/xco2noiseless_prec_plume_winds__linear/scaler.save']

## Model X

In [21]:
exp_name = "xco2noiseless_prec_plume_winds_modelX"
wandb.init(project=project_name, name=exp_name)

In [22]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [23]:
inputs = tf.keras.layers.Input((64, 64, 5))

x = tf.keras.layers.Conv2D(32, kernel_size=(3, 3), activation="elu", strides=1)(inputs)
x = tf.keras.layers.Dropout(0.1)(x)
x = tf.keras.layers.Conv2D(32, kernel_size=(3, 3), activation="elu", strides=1)(x)
x = tf.keras.layers.MaxPooling2D(pool_size=(2, 2), padding="valid", strides=2)(x)
x = tf.keras.layers.BatchNormalization()(x)

x = tf.keras.layers.Conv2D(32, kernel_size=(3, 3), activation="elu", strides=1)(x)
x = tf.keras.layers.Dropout(0.2)(x)
x = tf.keras.layers.Conv2D(64, kernel_size=(3, 3), activation="elu", strides=1)(x)
x = tf.keras.layers.BatchNormalization()(x)

x = tf.keras.layers.Conv2D(64, kernel_size=(3, 3), activation="elu", strides=1)(x)
x = tf.keras.layers.Dropout(0.2)(x)
x = tf.keras.layers.Conv2D(64, kernel_size=(3, 3), activation="elu", strides=1)(x)
x = tf.keras.layers.MaxPooling2D(pool_size=(2, 2), padding="valid", strides=2)(x)

x = tf.keras.layers.Flatten()(x)
x = tf.keras.layers.Dense(1)(x)
outputs = tf.keras.layers.LeakyReLU(alpha=0.3)(x)

model = tf.keras.Model([inputs], outputs)

model.compile("adam", loss="MeanAbsoluteError")

### Train 

In [24]:
model.fit(
    data.x.train,
    data.y.train,
    epochs=500,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1,
)

Epoch 1/500


2023-02-14 19:35:22.076610: E tensorflow/core/grappler/optimizers/meta_optimizer.cc:954] layout failed: INVALID_ARGUMENT: Size of values 0 does not match size of permutation 4 @ fanin shape inmodel_1/dropout/dropout/SelectV2-2-TransposeNHWCToNCHW-LayoutOptimizer


386/393 [============================>.] - ETA: 0s - loss: 3.6133
Epoch 1: val_loss improved from inf to 4.33932, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/xco2noiseless_prec_plume_winds_modelX/w_best.h5
extra_val_loss: 2.97040057182312
393/393 [==============================] - 6s 9ms/step - loss: 3.6046 - val_loss: 4.3393
Epoch 2/500
391/393 [============================>.] - ETA: 0s - loss: 3.2037
Epoch 2: val_loss improved from 4.33932 to 3.77283, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/xco2noiseless_prec_plume_winds_modelX/w_best.h5
extra_val_loss: 4.264192581176758
393/393 [==============================] - 3s 8ms/step - loss: 3.2014 - val_loss: 3.7728
Epoch 3/500
390/393 [============================>.] - ETA: 0s - loss: 2.9877
Epoch 3: val_loss improved from 3.77283 to 3.13717, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/xco2noiseless_prec_plume_winds_modelX/w_best.h5
extra_val_loss: 4.707

### save

In [25]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))
joblib.dump(data.x.scaler, os.path.join(save_dir, exp_name, "scaler.save"))

['/cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/xco2noiseless_prec_plume_winds_modelX/scaler.save']

# FIELD NOISY + PERFECT SEG + FIELD PREC + WINDS

In [29]:
data = Data_train(path_train_nc, path_valid_nc, path_extra_valid_nc)
data.prepare_input(
    "xco2_noisy", "weighted_plume", "xco2_noisy_prec", "u_wind", "v_wind"
)
data.prepare_output_inversion()

data.x.train.shape (12576, 64, 64, 5)


## EfficientNetB0 - no gen

In [30]:
exp_name = "xco2_prec_plume_winds_Eff_nogen"
wandb.init(project=project_name, name=exp_name)

In [31]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [32]:
model_builder = rm.Keras_reg_model_builder("EfficientNetB0", data.x.train.shape[1:], 1)
model = model_builder.get_model()
model.compile("adam", loss=tf.keras.losses.MeanAbsoluteError())

/profils_cerea/dumontj/mambaforge/envs/gpu/lib/python3.9/site-packages/keras/applications/efficientnet.py:321: UserWarning: This model usually expects 1 or 3 input channels. However, it was passed an input_shape with 5 input channels.
  input_shape = imagenet_utils.obtain_input_shape(


### Train 

In [33]:
model.fit(
    data.x.train,
    data.y.train,
    epochs=500,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1,
)

Epoch 1/500


2023-02-14 20:01:43.618724: E tensorflow/core/grappler/optimizers/meta_optimizer.cc:954] layout failed: INVALID_ARGUMENT: Size of values 0 does not match size of permutation 4 @ fanin shape inmodel_3/efficientnetb0/block2b_drop/dropout/SelectV2-2-TransposeNHWCToNCHW-LayoutOptimizer


393/393 [==============================] - ETA: 0s - loss: 4.0673
Epoch 1: val_loss improved from inf to 4.05533, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/xco2_prec_plume_winds_Eff_nogen/w_best.h5
extra_val_loss: 5.620512008666992
393/393 [==============================] - 35s 43ms/step - loss: 4.0673 - val_loss: 4.0553
Epoch 2/500
393/393 [==============================] - ETA: 0s - loss: 3.2499
Epoch 2: val_loss did not improve from 4.05533
extra_val_loss: 8.402103424072266
393/393 [==============================] - 15s 38ms/step - loss: 3.2499 - val_loss: 4.1304
Epoch 3/500
393/393 [==============================] - ETA: 0s - loss: 2.9661
Epoch 3: val_loss improved from 4.05533 to 2.82050, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/xco2_prec_plume_winds_Eff_nogen/w_best.h5
extra_val_loss: 6.869321823120117
393/393 [==============================] - 16s 42ms/step - loss: 2.9661 - val_loss: 2.8205
Epoch 4/500
393/393 [=======

### save

In [34]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))
joblib.dump(data.x.scaler, os.path.join(save_dir, exp_name, "scaler.save"))

['/cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/xco2_prec_plume_winds_Eff_nogen/scaler.save']

## EfficientNetB0 - with gen

In [35]:
exp_name = "xco2_prec_plume_winds_Eff_gen"
wandb.init(project=project_name, name=exp_name)

In [36]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [37]:
model_builder = rm.Keras_reg_model_builder("EfficientNetB0", data.x.train.shape[1:], 1)
model = model_builder.get_model()
model.compile("adam", loss=tf.keras.losses.MeanAbsoluteError())

/profils_cerea/dumontj/mambaforge/envs/gpu/lib/python3.9/site-packages/keras/applications/efficientnet.py:321: UserWarning: This model usually expects 1 or 3 input channels. However, it was passed an input_shape with 5 input channels.
  input_shape = imagenet_utils.obtain_input_shape(


### Train 

In [38]:
model.fit(
    generator.flow(data.x.train, data.y.train),
    epochs=1000,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1,
)

Epoch 1/1000


/profils_cerea/dumontj/mambaforge/envs/gpu/lib/python3.9/site-packages/keras/preprocessing/image.py:766: UserWarning: NumpyArrayIterator is set to use the data format convention "channels_last" (channels on axis 3), i.e. expected either 1, 3, or 4 channels on axis 3. However, it was passed an array with shape (12576, 64, 64, 5) (5 channels).
  warnings.warn(
2023-02-14 21:58:23.811248: E tensorflow/core/grappler/optimizers/meta_optimizer.cc:954] layout failed: INVALID_ARGUMENT: Size of values 0 does not match size of permutation 4 @ fanin shape inmodel_4/efficientnetb0/block2b_drop/dropout/SelectV2-2-TransposeNHWCToNCHW-LayoutOptimizer


393/393 [==============================] - ETA: 0s - loss: 4.5516
Epoch 1: val_loss improved from inf to 4.73140, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/xco2_prec_plume_winds_Eff_gen/w_best.h5
extra_val_loss: 2.5423214435577393
393/393 [==============================] - 41s 55ms/step - loss: 4.5516 - val_loss: 4.7314
Epoch 2/1000
393/393 [==============================] - ETA: 0s - loss: 3.6826
Epoch 2: val_loss improved from 4.73140 to 3.69973, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/xco2_prec_plume_winds_Eff_gen/w_best.h5
extra_val_loss: 4.405259132385254
393/393 [==============================] - 20s 50ms/step - loss: 3.6826 - val_loss: 3.6997
Epoch 3/1000
393/393 [==============================] - ETA: 0s - loss: 3.4638
Epoch 3: val_loss did not improve from 3.69973
extra_val_loss: 19.252315521240234
393/393 [==============================] - 20s 52ms/step - loss: 3.4638 - val_loss: 17.4724
Epoch 4/1000
393/393 [=====

### save

In [39]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))
joblib.dump(data.x.scaler, os.path.join(save_dir, exp_name, "scaler.save"))

['/cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/xco2_prec_plume_winds_Eff_gen/scaler.save']

## Linear baseline

In [40]:
exp_name = "xco2_prec_plume_winds_linear"
wandb.init(project=project_name, name=exp_name)

In [41]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [42]:
model = tf.keras.models.Sequential()
model.add(tf.keras.layers.Conv2D(16, (3, 3), input_shape=data.x.fields_input_shape))
model.add(tf.keras.layers.MaxPooling2D((2, 2)))
model.add(tf.keras.layers.Conv2D(16, (3, 3)))
model.add(tf.keras.layers.MaxPooling2D((2, 2)))
model.add(tf.keras.layers.Conv2D(16, (3, 3)))
model.add(tf.keras.layers.Flatten())
model.add(tf.keras.layers.Dense(16))
model.add(tf.keras.layers.Dense(1))

model.compile("adam", loss="MeanAbsoluteError")

### Train 

In [43]:
model.fit(
    data.x.train,
    data.y.train,
    epochs=200,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1,
)

Epoch 1/200
388/393 [============================>.] - ETA: 0s - loss: 3.9570
Epoch 1: val_loss improved from inf to 3.51325, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/xco2_prec_plume_winds_linear/w_best.h5
extra_val_loss: 5.586289405822754
393/393 [==============================] - 3s 6ms/step - loss: 3.9453 - val_loss: 3.5132
Epoch 2/200
385/393 [============================>.] - ETA: 0s - loss: 3.3281
Epoch 2: val_loss improved from 3.51325 to 3.12507, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/xco2_prec_plume_winds_linear/w_best.h5
extra_val_loss: 6.519186496734619
393/393 [==============================] - 2s 5ms/step - loss: 3.3255 - val_loss: 3.1251
Epoch 3/200
391/393 [============================>.] - ETA: 0s - loss: 3.1840
Epoch 3: val_loss improved from 3.12507 to 2.99035, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/xco2_prec_plume_winds_linear/w_best.h5
extra_val_loss: 6.1529974937438965


### save

In [44]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))
joblib.dump(data.x.scaler, os.path.join(save_dir, exp_name, "scaler.save"))

['/cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/xco2_prec_plume_winds_linear/scaler.save']

## Model X

In [45]:
exp_name = "xco2_prec_plume_winds_modelX"
wandb.init(project=project_name, name=exp_name)

In [46]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [47]:
inputs = tf.keras.layers.Input((64, 64, 5))

x = tf.keras.layers.Conv2D(32, kernel_size=(3, 3), activation="elu", strides=1)(inputs)
x = tf.keras.layers.Dropout(0.1)(x)
x = tf.keras.layers.Conv2D(32, kernel_size=(3, 3), activation="elu", strides=1)(x)
x = tf.keras.layers.MaxPooling2D(pool_size=(2, 2), padding="valid", strides=2)(x)
x = tf.keras.layers.BatchNormalization()(x)

x = tf.keras.layers.Conv2D(32, kernel_size=(3, 3), activation="elu", strides=1)(x)
x = tf.keras.layers.Dropout(0.2)(x)
x = tf.keras.layers.Conv2D(64, kernel_size=(3, 3), activation="elu", strides=1)(x)
x = tf.keras.layers.BatchNormalization()(x)

x = tf.keras.layers.Conv2D(64, kernel_size=(3, 3), activation="elu", strides=1)(x)
x = tf.keras.layers.Dropout(0.2)(x)
x = tf.keras.layers.Conv2D(64, kernel_size=(3, 3), activation="elu", strides=1)(x)
x = tf.keras.layers.MaxPooling2D(pool_size=(2, 2), padding="valid", strides=2)(x)

x = tf.keras.layers.Flatten()(x)
x = tf.keras.layers.Dense(1)(x)
outputs = tf.keras.layers.LeakyReLU(alpha=0.3)(x)

model = tf.keras.Model([inputs], outputs)

model.compile("adam", loss="MeanAbsoluteError")

### Train 

In [48]:
model.fit(
    data.x.train,
    data.y.train,
    epochs=500,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1,
)

Epoch 1/500


2023-02-15 03:29:55.967463: E tensorflow/core/grappler/optimizers/meta_optimizer.cc:954] layout failed: INVALID_ARGUMENT: Size of values 0 does not match size of permutation 4 @ fanin shape inmodel_5/dropout_3/dropout/SelectV2-2-TransposeNHWCToNCHW-LayoutOptimizer


388/393 [============================>.] - ETA: 0s - loss: 3.7345
Epoch 1: val_loss improved from inf to 5.69719, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/xco2_prec_plume_winds_modelX/w_best.h5
extra_val_loss: 2.9317948818206787
393/393 [==============================] - 5s 9ms/step - loss: 3.7325 - val_loss: 5.6972
Epoch 2/500
393/393 [==============================] - ETA: 0s - loss: 3.3064
Epoch 2: val_loss improved from 5.69719 to 4.67199, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/xco2_prec_plume_winds_modelX/w_best.h5
extra_val_loss: 4.198660850524902
393/393 [==============================] - 3s 8ms/step - loss: 3.3064 - val_loss: 4.6720
Epoch 3/500
387/393 [============================>.] - ETA: 0s - loss: 3.1132
Epoch 3: val_loss improved from 4.67199 to 3.82691, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/xco2_prec_plume_winds_modelX/w_best.h5
extra_val_loss: 5.734956741333008
393/393 [===

### save

In [49]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))
joblib.dump(data.x.scaler, os.path.join(save_dir, exp_name, "scaler.save"))

['/cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/xco2_prec_plume_winds_modelX/scaler.save']

## Eval

In [ ]:
path_eval_nc = path_extra_valid_nc
exp_name = "plume_Eff_nogen"

data = Data_eval(path_eval_nc)
data.prepare_input(model_eval.get_scaler(os.path.join(save_dir, exp_name)), "plume")
data.prepare_output_inversion()
model = model_eval.get_inversion_model(
    os.path.join(save_dir, exp_name), name_w="w_best.h5"
)

In [ ]:
metrics = model_eval.get_inv_metrics_model_on_data(model, data)
print("mae:", np.mean(metrics["mae"]))
print("mape:", np.mean(metrics["mape"]))

In [ ]:
mean_metrics = model_eval.get_inv_mean_loss(data)
print("mae:", np.mean(mean_metrics["mae"]))
print("mape:", np.mean(mean_metrics["mape"]))

In [ ]:
model_eval.get_summary_histo_inversion(model, data)

# FIELD NOT NOISY + GUESS SEG

# FIELD NOISY + GUESS SEG

# XCO2

In [6]:
data = Data_train(path_train_nc, path_valid_nc, path_extra_valid_nc)
data.prepare_input("xco2")
data.prepare_output_inversion()

2023-02-20 11:37:45.053709: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  SSE4.1 SSE4.2 AVX AVX2 AVX512F FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-02-20 11:37:45.621470: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1613] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 14490 MB memory:  -> device: 0, name: Quadro RTX 5000, pci bus id: 0000:65:00.0, compute capability: 7.5


data.x.train.shape (12576, 64, 64, 1)


## EfficientNetB0 - no gen

In [7]:
exp_name = "xco2_noisy_Eff_nogen"
wandb.init(project=project_name, name=exp_name)

Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: Currently logged in as: joffreydumont (cerea-daml). Use `wandb login --relogin` to force relogin


In [8]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [9]:
model_builder = rm.Keras_reg_model_builder("EfficientNetB0", data.x.train.shape[1:], 1)
model = model_builder.get_model()
model.compile("adam", loss=tf.keras.losses.MeanAbsoluteError())

2023-02-13 09:34:03.116182: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  SSE4.1 SSE4.2 AVX AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-02-13 09:34:17.189794: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1613] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 25485 MB memory:  -> device: 0, name: NVIDIA A40, pci bus id: 0000:21:00.0, compute capability: 8.6


### Train 

In [10]:
model.fit(
    data.x.train,
    data.y.train,
    epochs=500,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1,
)

Epoch 1/500


2023-02-13 09:34:30.273865: E tensorflow/core/grappler/optimizers/meta_optimizer.cc:954] layout failed: INVALID_ARGUMENT: Size of values 0 does not match size of permutation 4 @ fanin shape inmodel/efficientnetb0/block2b_drop/dropout/SelectV2-2-TransposeNHWCToNCHW-LayoutOptimizer
2023-02-13 09:34:55.594642: I tensorflow/compiler/xla/stream_executor/cuda/cuda_dnn.cc:428] Loaded cuDNN version 8401
2023-02-13 09:35:18.539993: I tensorflow/tsl/platform/default/subprocess.cc:304] Start cannot spawn child process: No such file or directory
2023-02-13 09:35:20.929530: I tensorflow/compiler/xla/stream_executor/cuda/cuda_blas.cc:630] TensorFloat-32 will be used for the matrix multiplication. This will only be logged once.
2023-02-13 09:35:21.743544: I tensorflow/compiler/xla/service/service.cc:173] XLA service 0x7f8ada8988d0 initialized for platform CUDA (this does not guarantee that XLA will be used). Devices:
2023-02-13 09:35:21.743583: I tensorflow/compiler/xla/service/service.cc:181]   Stre

393/393 [==============================] - ETA: 0s - loss: 3.8738
Epoch 1: val_loss improved from inf to 5.33688, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_Eff_nogen/w_best.h5
extra_val_loss: 1.4520275592803955
393/393 [==============================] - 97s 44ms/step - loss: 3.8738 - val_loss: 5.3369
Epoch 2/500
393/393 [==============================] - ETA: 0s - loss: 2.8868
Epoch 2: val_loss did not improve from 5.33688
extra_val_loss: 1.8317114114761353
393/393 [==============================] - 14s 34ms/step - loss: 2.8868 - val_loss: 5.4245
Epoch 3/500
392/393 [============================>.] - ETA: 0s - loss: 2.8092
Epoch 3: val_loss did not improve from 5.33688
extra_val_loss: 3.102468490600586
393/393 [==============================] - 15s 38ms/step - loss: 2.8078 - val_loss: 6.2284
Epoch 4/500
393/393 [==============================] - ETA: 0s - loss: 2.5587
Epoch 4: val_loss improved from 5.33688 to 2.45140, saving model to /cerea_raid/use

### save

In [11]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))
joblib.dump(data.x.scaler, os.path.join(save_dir, exp_name, "scaler.save"))

['/cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_Eff_nogen/scaler.save']

## EfficientNetB0 - with gen

In [12]:
exp_name = "xco2_noisy_Eff_gen"
wandb.init(project=project_name, name=exp_name)

In [13]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [14]:
model_builder = rm.Keras_reg_model_builder("EfficientNetB0", data.x.train.shape[1:], 1)
model = model_builder.get_model()
model.compile("adam", loss=tf.keras.losses.MeanAbsoluteError())

### Train 

In [15]:
model.fit(
    generator.flow(data.x.train, data.y.train),
    epochs=1000,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1,
)

Epoch 1/1000


2023-02-13 11:44:20.891765: E tensorflow/core/grappler/optimizers/meta_optimizer.cc:954] layout failed: INVALID_ARGUMENT: Size of values 0 does not match size of permutation 4 @ fanin shape inmodel_1/efficientnetb0/block2b_drop/dropout/SelectV2-2-TransposeNHWCToNCHW-LayoutOptimizer


393/393 [==============================] - ETA: 0s - loss: 4.2316
Epoch 1: val_loss improved from inf to 4.91550, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_Eff_gen/w_best.h5
extra_val_loss: 2.102231025695801
393/393 [==============================] - 39s 53ms/step - loss: 4.2316 - val_loss: 4.9155
Epoch 2/1000
392/393 [============================>.] - ETA: 0s - loss: 3.1995
Epoch 2: val_loss did not improve from 4.91550
extra_val_loss: 2.1254639625549316
393/393 [==============================] - 20s 51ms/step - loss: 3.1995 - val_loss: 5.4380
Epoch 3/1000
392/393 [============================>.] - ETA: 0s - loss: 3.0561
Epoch 3: val_loss improved from 4.91550 to 4.58871, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_Eff_gen/w_best.h5
extra_val_loss: 1.8833814859390259
393/393 [==============================] - 20s 51ms/step - loss: 3.0552 - val_loss: 4.5887
Epoch 4/1000
393/393 [==============================] - ETA:

### save

In [16]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))
joblib.dump(data.x.scaler, os.path.join(save_dir, exp_name, "scaler.save"))

['/cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_Eff_gen/scaler.save']

## Linear baseline

In [17]:
exp_name = "xco2_noisy_linear"
wandb.init(project=project_name, name=exp_name)

In [18]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [19]:
model = tf.keras.models.Sequential()
model.add(tf.keras.layers.Conv2D(16, (3, 3), input_shape=data.x.fields_input_shape))
model.add(tf.keras.layers.MaxPooling2D((2, 2)))
model.add(tf.keras.layers.Conv2D(16, (3, 3)))
model.add(tf.keras.layers.MaxPooling2D((2, 2)))
model.add(tf.keras.layers.Conv2D(16, (3, 3)))
model.add(tf.keras.layers.Flatten())
model.add(tf.keras.layers.Dense(16))
model.add(tf.keras.layers.Dense(1))

model.compile("adam", loss="MeanAbsoluteError")

### Train 

In [20]:
model.fit(
    data.x.train,
    data.y.train,
    epochs=200,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1,
)

Epoch 1/200
384/393 [============================>.] - ETA: 0s - loss: 3.7989
Epoch 1: val_loss improved from inf to 3.48380, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_linear/w_best.h5
extra_val_loss: 4.0431342124938965
393/393 [==============================] - 3s 5ms/step - loss: 3.7961 - val_loss: 3.4838
Epoch 2/200
382/393 [============================>.] - ETA: 0s - loss: 3.3576
Epoch 2: val_loss did not improve from 3.48380
extra_val_loss: 5.233192443847656
393/393 [==============================] - 2s 4ms/step - loss: 3.3493 - val_loss: 3.5015
Epoch 3/200
379/393 [===========================>..] - ETA: 0s - loss: 3.2980
Epoch 3: val_loss improved from 3.48380 to 3.35223, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_linear/w_best.h5
extra_val_loss: 5.039037227630615
393/393 [==============================] - 2s 4ms/step - loss: 3.2964 - val_loss: 3.3522
Epoch 4/200
380/393 [============================>.] - ETA:

### save

In [21]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))
joblib.dump(data.x.scaler, os.path.join(save_dir, exp_name, "scaler.save"))

['/cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_linear/scaler.save']

## Research of a new model

In [12]:
exp_name = "xco2_noisy_modelX"
wandb.init(project=project_name, name=exp_name)

Problem at: /tmp/ipykernel_1410243/4155257584.py 2 <module>


KeyboardInterrupt: 

Error in callback <bound method AutoreloadMagics.post_execute_hook of <IPython.extensions.autoreload.AutoreloadMagics object at 0x7f7e4fdee7c0>> (for post_execute):


KeyboardInterrupt: 

In [8]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [9]:
reg_builder = rm.Reg_model_builder(
    "essential",
    data.x.fields_input_shape,
    data.y.classes,
    data.x.n_layer,
    data.x.xco2_noisy_chans,
)
model = reg_builder.get_model()
model.compile("adam", "MeanAbsoluteError")

### Train 

In [10]:
model.fit(
    data.x.train,
    data.y.train,
    epochs=1000,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1,
)

Epoch 1/500


2023-02-20 11:38:01.953264: E tensorflow/core/grappler/optimizers/meta_optimizer.cc:954] layout failed: INVALID_ARGUMENT: Size of values 0 does not match size of permutation 4 @ fanin shape inmodel_1/model/dropout/dropout/SelectV2-2-TransposeNHWCToNCHW-LayoutOptimizer
2023-02-20 11:38:02.699351: I tensorflow/compiler/xla/stream_executor/cuda/cuda_dnn.cc:428] Loaded cuDNN version 8401
2023-02-20 11:38:03.261296: I tensorflow/tsl/platform/default/subprocess.cc:304] Start cannot spawn child process: No such file or directory
2023-02-20 11:38:03.609277: I tensorflow/compiler/xla/service/service.cc:173] XLA service 0x7f77996df360 initialized for platform CUDA (this does not guarantee that XLA will be used). Devices:
2023-02-20 11:38:03.609305: I tensorflow/compiler/xla/service/service.cc:181]   StreamExecutor device (0): Quadro RTX 5000, Compute Capability 7.5
2023-02-20 11:38:03.612774: I tensorflow/compiler/mlir/tensorflow/utils/dump_mlir_util.cc:268] disabling MLIR crash reproducer, set 

391/393 [============================>.] - ETA: 0s - loss: 4.4488
Epoch 1: val_loss improved from inf to 4.30865, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_modelX/w_best.h5
extra_val_loss: 3.0225837230682373
393/393 [==============================] - 10s 13ms/step - loss: 4.4493 - val_loss: 4.3087
Epoch 2/500
391/393 [============================>.] - ETA: 0s - loss: 4.2343
Epoch 2: val_loss did not improve from 4.30865
extra_val_loss: 2.441567897796631
393/393 [==============================] - 5s 12ms/step - loss: 4.2364 - val_loss: 4.3639
Epoch 3/500
391/393 [============================>.] - ETA: 0s - loss: 4.1681
Epoch 3: val_loss improved from 4.30865 to 4.17098, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_modelX/w_best.h5
extra_val_loss: 3.3424787521362305
393/393 [==============================] - 5s 13ms/step - loss: 4.1620 - val_loss: 4.1710
Epoch 4/500
391/393 [============================>.] - ETA: 0s - l

### save

In [13]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))

# XCO2 - XCO2_prec - winds

In [22]:
data = Data_train(path_train_nc, path_valid_nc, path_extra_valid_nc)
data.prepare_input("xco2", "xco2_prec", "u_wind", "v_wind")
data.prepare_output_inversion()

data.x.train.shape (12576, 64, 64, 4)


## EfficientNetB0 - no gen

In [7]:
exp_name = "xco2_prec_winds_noisy_Eff_nogen"
wandb.init(project=project_name, name=exp_name)

Failed to detect the name of this notebook, you can set it manually with the WANDB_NOTEBOOK_NAME environment variable to enable code saving.
wandb: Currently logged in as: joffreydumont (cerea-daml). Use `wandb login --relogin` to force relogin


In [8]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [9]:
model_builder = rm.Keras_reg_model_builder("EfficientNetB0", data.x.train.shape[1:], 1)
model = model_builder.get_model()
model.compile("adam", loss=tf.keras.losses.MeanAbsoluteError())

2023-02-13 09:34:03.116182: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  SSE4.1 SSE4.2 AVX AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-02-13 09:34:17.189794: I tensorflow/core/common_runtime/gpu/gpu_device.cc:1613] Created device /job:localhost/replica:0/task:0/device:GPU:0 with 25485 MB memory:  -> device: 0, name: NVIDIA A40, pci bus id: 0000:21:00.0, compute capability: 8.6


### Train 

In [10]:
model.fit(
    data.x.train,
    data.y.train,
    epochs=500,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1,
)

Epoch 1/500


2023-02-13 09:34:30.273865: E tensorflow/core/grappler/optimizers/meta_optimizer.cc:954] layout failed: INVALID_ARGUMENT: Size of values 0 does not match size of permutation 4 @ fanin shape inmodel/efficientnetb0/block2b_drop/dropout/SelectV2-2-TransposeNHWCToNCHW-LayoutOptimizer
2023-02-13 09:34:55.594642: I tensorflow/compiler/xla/stream_executor/cuda/cuda_dnn.cc:428] Loaded cuDNN version 8401
2023-02-13 09:35:18.539993: I tensorflow/tsl/platform/default/subprocess.cc:304] Start cannot spawn child process: No such file or directory
2023-02-13 09:35:20.929530: I tensorflow/compiler/xla/stream_executor/cuda/cuda_blas.cc:630] TensorFloat-32 will be used for the matrix multiplication. This will only be logged once.
2023-02-13 09:35:21.743544: I tensorflow/compiler/xla/service/service.cc:173] XLA service 0x7f8ada8988d0 initialized for platform CUDA (this does not guarantee that XLA will be used). Devices:
2023-02-13 09:35:21.743583: I tensorflow/compiler/xla/service/service.cc:181]   Stre

393/393 [==============================] - ETA: 0s - loss: 3.8738
Epoch 1: val_loss improved from inf to 5.33688, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_Eff_nogen/w_best.h5
extra_val_loss: 1.4520275592803955
393/393 [==============================] - 97s 44ms/step - loss: 3.8738 - val_loss: 5.3369
Epoch 2/500
393/393 [==============================] - ETA: 0s - loss: 2.8868
Epoch 2: val_loss did not improve from 5.33688
extra_val_loss: 1.8317114114761353
393/393 [==============================] - 14s 34ms/step - loss: 2.8868 - val_loss: 5.4245
Epoch 3/500
392/393 [============================>.] - ETA: 0s - loss: 2.8092
Epoch 3: val_loss did not improve from 5.33688
extra_val_loss: 3.102468490600586
393/393 [==============================] - 15s 38ms/step - loss: 2.8078 - val_loss: 6.2284
Epoch 4/500
393/393 [==============================] - ETA: 0s - loss: 2.5587
Epoch 4: val_loss improved from 5.33688 to 2.45140, saving model to /cerea_raid/use

### save

In [11]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))
joblib.dump(data.x.scaler, os.path.join(save_dir, exp_name, "scaler.save"))

['/cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_Eff_nogen/scaler.save']

## EfficientNetB0 - with gen

In [12]:
exp_name = "xco2_prec_winds_noisy_Eff_gen"
wandb.init(project=project_name, name=exp_name)

In [13]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [14]:
model_builder = rm.Keras_reg_model_builder("EfficientNetB0", data.x.train.shape[1:], 1)
model = model_builder.get_model()
model.compile("adam", loss=tf.keras.losses.MeanAbsoluteError())

### Train 

In [15]:
model.fit(
    generator.flow(data.x.train, data.y.train),
    epochs=1000,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1,
)

Epoch 1/1000


2023-02-13 11:44:20.891765: E tensorflow/core/grappler/optimizers/meta_optimizer.cc:954] layout failed: INVALID_ARGUMENT: Size of values 0 does not match size of permutation 4 @ fanin shape inmodel_1/efficientnetb0/block2b_drop/dropout/SelectV2-2-TransposeNHWCToNCHW-LayoutOptimizer


393/393 [==============================] - ETA: 0s - loss: 4.2316
Epoch 1: val_loss improved from inf to 4.91550, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_Eff_gen/w_best.h5
extra_val_loss: 2.102231025695801
393/393 [==============================] - 39s 53ms/step - loss: 4.2316 - val_loss: 4.9155
Epoch 2/1000
392/393 [============================>.] - ETA: 0s - loss: 3.1995
Epoch 2: val_loss did not improve from 4.91550
extra_val_loss: 2.1254639625549316
393/393 [==============================] - 20s 51ms/step - loss: 3.1995 - val_loss: 5.4380
Epoch 3/1000
392/393 [============================>.] - ETA: 0s - loss: 3.0561
Epoch 3: val_loss improved from 4.91550 to 4.58871, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_Eff_gen/w_best.h5
extra_val_loss: 1.8833814859390259
393/393 [==============================] - 20s 51ms/step - loss: 3.0552 - val_loss: 4.5887
Epoch 4/1000
393/393 [==============================] - ETA:

### save

In [16]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))
joblib.dump(data.x.scaler, os.path.join(save_dir, exp_name, "scaler.save"))

['/cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_Eff_gen/scaler.save']

## Linear baseline

In [17]:
exp_name = "xco2_prec_winds_noisy_linear"
wandb.init(project=project_name, name=exp_name)

In [18]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [19]:
model = tf.keras.models.Sequential()
model.add(tf.keras.layers.Conv2D(16, (3, 3), input_shape=data.x.fields_input_shape))
model.add(tf.keras.layers.MaxPooling2D((2, 2)))
model.add(tf.keras.layers.Conv2D(16, (3, 3)))
model.add(tf.keras.layers.MaxPooling2D((2, 2)))
model.add(tf.keras.layers.Conv2D(16, (3, 3)))
model.add(tf.keras.layers.Flatten())
model.add(tf.keras.layers.Dense(16))
model.add(tf.keras.layers.Dense(1))

model.compile("adam", loss="MeanAbsoluteError")

### Train 

In [20]:
model.fit(
    data.x.train,
    data.y.train,
    epochs=200,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1,
)

Epoch 1/200
384/393 [============================>.] - ETA: 0s - loss: 3.7989
Epoch 1: val_loss improved from inf to 3.48380, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_linear/w_best.h5
extra_val_loss: 4.0431342124938965
393/393 [==============================] - 3s 5ms/step - loss: 3.7961 - val_loss: 3.4838
Epoch 2/200
382/393 [============================>.] - ETA: 0s - loss: 3.3576
Epoch 2: val_loss did not improve from 3.48380
extra_val_loss: 5.233192443847656
393/393 [==============================] - 2s 4ms/step - loss: 3.3493 - val_loss: 3.5015
Epoch 3/200
379/393 [===========================>..] - ETA: 0s - loss: 3.2980
Epoch 3: val_loss improved from 3.48380 to 3.35223, saving model to /cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_linear/w_best.h5
extra_val_loss: 5.039037227630615
393/393 [==============================] - 2s 4ms/step - loss: 3.2964 - val_loss: 3.3522
Epoch 4/200
380/393 [============================>.] - ETA:

### save

In [21]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))
joblib.dump(data.x.scaler, os.path.join(save_dir, exp_name, "scaler.save"))

['/cerea_raid/users/dumontj/dev/coco2/dl/nb_train/sim/pat/plume_linear/scaler.save']

## Research of a new model

In [23]:
exp_name = "xco2_prec_winds_noisy_modelX"
wandb.init(project=project_name, name=exp_name)

In [24]:
cbs = get_modelcheckpoint(True, [], os.path.join(save_dir, exp_name, "w_best.h5"))
history = ExtraValidation((data.x.extra_valid, data.y.extra_valid))
cbs.append(WandbMetricsLogger())
cbs.append(history)

In [25]:
reg_builder = rm.Reg_model_builder(
    "essential",
    data.x.fields_input_shape,
    data.y.classes,
    data.x.n_layer,
    data.x.xco2_noisy_chans,
)
model = reg_builder.get_model()
model.compile("adam", "MeanAbsoluteError")

### Train 

In [27]:
model.fit(
    data.x.train,
    data.y.train,
    epochs=2000,
    callbacks=cbs,
    validation_data=(data.x.valid, data.y.valid),
    verbose=1,
)

Epoch 1/2000
  1/393 [..............................] - ETA: 5s - loss: 2.0615

KeyboardInterrupt: 

### save

In [29]:
model.save(os.path.join(save_dir, exp_name, "w_last.h5"))